In [4]:
%pip install pandas
%pip install requests


[notice] A new release of pip available: 22.3.1 -> 23.1.2
[notice] To update, run: python3.11 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.
  Using cached requests-2.29.0-py3-none-any.whl (62 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.7/121.7 kB 3.2 MB/s eta 0:00:00
  Using cached idna-3.4-py3-none-any.whl (61 kB)
  Using cached urllib3-1.26.15-py2.py3-none-any.whl (140 kB)
  Using cached certifi-2022.12.7-py3-none-any.whl (155 kB)

[notice] A new release of pip available: 22.3.1 -> 23.1.2
[notice] To update, run: python3.11 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [20]:
import math

# get data for 10 days.
import requests
import csv
import numpy as np
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

In [1]:


import pandas as pd
# Load JSON data from file
with open('data.json', 'r') as file:
    json_data = file.read()

# Convert JSON data to DataFrame
df = pd.read_json(json_data)
# Save DataFrame to CSV file
df.to_csv('data.csv', index=False)


[notice] A new release of pip available: 22.3.1 -> 23.1.2
[notice] To update, run: python3.11 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [5]:
import pandas as pd

df = pd.read_csv('data_jan_10_days.csv')
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20211 entries, 0 to 20210
Data columns (total 22 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   time             20211 non-null  object 
 1   segment_id       20211 non-null  int64  
 2   speed            20211 non-null  int64  
 3   street           20211 non-null  object 
 4   direction        20211 non-null  object 
 5   from_street      20211 non-null  object 
 6   to_street        20211 non-null  object 
 7   length           20211 non-null  float64
 8   street_heading   20211 non-null  object 
 9   bus_count        20211 non-null  int64  
 10  message_count    20211 non-null  int64  
 11  hour             20211 non-null  int64  
 12  day_of_week      20211 non-null  int64  
 13  month            20211 non-null  int64  
 14  record_id        20211 non-null  object 
 15  start_latitude   20211 non-null  float64
 16  start_longitude  20211 non-null  float64
 17  end_latitude

In [25]:
# get segments_street_mapping
import requests
import csv

filename = "segment_street_mapping.csv"

# Set the API endpoint URL
url = 'https://data.cityofchicago.org/resource/sxs8-h27x.json'

# Set the query parameters to filter the data by time range
# "time between '2023-01-01T00:00:00' and '2023-02-01T00:00:00'"
params = {
'$where': f"time between '2023-04-28T00:00:00' and '2023-05-01T00:00:00' and speed != '-1'",
"$limit" : 100000,
'$select' : "distinct segment_id, street, from_street, to_street, start_latitude, start_longitude, end_latitude, end_longitude"

}

# Make the API call and get the response
response = requests.get(url, params=params)
# Check if the response was successful
if response.status_code == 200:
    data = response.json()
    with open(filename, 'w', newline='') as file:
        fieldnames = list(data[0].keys())
        writer = csv.DictWriter(file, fieldnames=fieldnames)

        # Write header row
        writer.writeheader()

        # Write data rows
        writer.writerows(data)
else:
# Print an error message if the API call failed
    print('API call failed with status code:', response.status_code)

99

In [7]:
# Analyse segements and streets

# assume df is the DataFrame containing the segment data with columns segment_id, street, from_street, to_street
df = pd.read_csv('segment_street_mapping.csv')
df_sorted = df.sort_values(by=['street', 'segment_id'])

prev_segment_id = -1
prev_street = ''

for index, row in df_sorted.iterrows():
    if row['street'] == prev_street:
        if row['segment_id'] - prev_segment_id == 1:
            print(f"Segments {prev_segment_id} and {row['segment_id']} are contiguous on street {row['street']}")
        else:
            print(f"Segments {prev_segment_id} and {row['segment_id']} are not contiguous on street {row['street']}")
    prev_segment_id = row['segment_id']
    prev_street = row['street']


Segments 477 and 478 are contiguous on street 111th
Segments 478 and 479 are contiguous on street 111th
Segments 479 and 480 are contiguous on street 111th
Segments 480 and 481 are contiguous on street 111th
Segments 481 and 482 are contiguous on street 111th
Segments 482 and 483 are contiguous on street 111th
Segments 483 and 484 are contiguous on street 111th
Segments 484 and 485 are contiguous on street 111th
Segments 485 and 486 are contiguous on street 111th
Segments 486 and 487 are contiguous on street 111th
Segments 487 and 488 are contiguous on street 111th
Segments 488 and 489 are contiguous on street 111th
Segments 489 and 490 are contiguous on street 111th
Segments 490 and 1115 are not contiguous on street 111th
Segments 1115 and 1116 are contiguous on street 111th
Segments 1116 and 1117 are contiguous on street 111th
Segments 1117 and 1118 are contiguous on street 111th
Segments 1081 and 1089 are not contiguous on street 127th
Segments 1082 and 1090 are not contiguous on st

In [16]:
# find the nearest station

filename = "data_April_10_days.csv"

# Set the API endpoint URL
url = 'https://data.cityofchicago.org/resource/sxs8-h27x.json'


params = {
'$where': f"time between '2023-04-11T00:00:00' and '2023-04-15T00:00:00' and speed != '-1'",
"$limit" : 100000,
'$select' : "distinct segment_id, street, from_street, to_street, start_latitude, start_longitude, end_latitude, end_longitude"

}

# Make the API call and get the response
response = requests.get(url, params=params)
# Check if the response was successful
if response.status_code == 200:
    data = response.json()
    with open(filename, 'w', newline='') as file:
        fieldnames = list(data[0].keys())
        writer = csv.DictWriter(file, fieldnames=fieldnames)

        # Write header row
        writer.writeheader()

        # Write data rows
        writer.writerows(data)
else:
# Print an error message if the API call failed
    print('API call failed with status code:', response.status_code)

df = pd.read_csv(filename)
print("The collected data dicreption ", df.info())
# Define the threshold distance for "near" in meters
NEAR_DISTANCE = 10000

# Define the latitude and longitude of the location you want to search near
latitude = 41.901997
longitude = -87.622817

# Calculate the Haversine distance between two points in meters
def haversine_distance(lat1, lon1, lat2, lon2):
    R = 6371e3  # Radius of the earth in km
    dLat = math.radians(lat2 - lat1)
    dLon = math.radians(lon2 - lon1)
    a = math.sin(dLat / 2) * math.sin(dLat / 2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dLon / 2) * math.sin(dLon / 2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    d = R * c  # Distance in meters
    return d

# Calculate the distance between each segment's start and end locations and the given location
distances = np.array([])
for _, row in df.iterrows():
    start_lat = row['start_latitude']
    start_lon = row['start_longitude']
    end_lat = row['end_latitude']
    end_lon = row['end_longitude']

    start_distance = haversine_distance(latitude, longitude, start_lat, start_lon)
    end_distance = haversine_distance(latitude, longitude, end_lat, end_lon)

    distances = np.append(distances, min(start_distance, end_distance))
    print(distances)

# Filter the segments based on the threshold distance
near_segments = df[distances <= NEAR_DISTANCE]

# Print the near segments
print(near_segments)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1038 entries, 0 to 1037
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   segment_id       1038 non-null   int64  
 1   street           1038 non-null   object 
 2   from_street      1038 non-null   object 
 3   to_street        1038 non-null   object 
 4   start_latitude   1038 non-null   float64
 5   start_longitude  1038 non-null   float64
 6   end_latitude     1038 non-null   float64
 7   end_longitude    1038 non-null   float64
dtypes: float64(4), int64(1), object(3)
memory usage: 65.0+ KB
The collected data dicreption  None
[8698.24924928]
[ 8698.24924928 19164.05540711]
[ 8698.24924928 19164.05540711 19688.46628692]
[ 8698.24924928 19164.05540711 19688.46628692  1251.80600302]
[ 8698.24924928 19164.05540711 19688.46628692  1251.80600302
 10407.95640456]
[ 8698.24924928 19164.05540711 19688.46628692  1251.80600302
 10407.95640456 11172.33966665]
[ 8698.

In [26]:
# seperate segments based on weather stations

filename = "segment_street_mapping.csv"



df = pd.read_csv(filename)
print("The collected data dicreption ", df.info())
# Define the threshold distance for "near" in meters
NEAR_DISTANCE = 10000


# Calculate the Haversine distance between two points in meters
def haversine_distance(lat1, lon1, lat2, lon2):
    R = 6371e3  # Radius of the earth in km
    dLat = math.radians(lat2 - lat1)
    dLon = math.radians(lon2 - lon1)
    a = math.sin(dLat / 2) * math.sin(dLat / 2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dLon / 2) * math.sin(dLon / 2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    d = R * c  # Distance in meters
    return d

weather_stations = [(41.976464, -87.647525)]
# Find the segments near each latitude and longitude pair
for lat, lon in weather_stations:
    distances = np.array([])
    print(f"Processing weather station at -  ({lat}, {lon}):")
    for _, row in df.iterrows():
        start_lat = row['start_latitude']
        start_lon = row['start_longitude']
        end_lat = row['end_latitude']
        end_lon = row['end_longitude']

        start_distance = haversine_distance(lat, lon, start_lat, start_lon)
        end_distance = haversine_distance(lat, lon, end_lat, end_lon)

        distances = np.append(distances, min(start_distance, end_distance))

    # Filter the segments based on the threshold distance
    near_segments = df[distances <= NEAR_DISTANCE]

    # Print the near segments
    print(f"Segments near ({lat}, {lon}):")
    print(near_segments)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1032 entries, 0 to 1031
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   segment_id       1032 non-null   int64  
 1   street           1032 non-null   object 
 2   from_street      1032 non-null   object 
 3   to_street        1032 non-null   object 
 4   start_latitude   1032 non-null   float64
 5   start_longitude  1032 non-null   float64
 6   end_latitude     1032 non-null   float64
 7   end_longitude    1032 non-null   float64
dtypes: float64(4), int64(1), object(3)
memory usage: 64.6+ KB
The collected data dicreption  None
Processing weather station at -  (41.976464, -87.647525):
Segments near (41.976464, -87.647525):
      segment_id       street from_street  to_street  start_latitude   
1            365      Western    Lawrence     Foster       41.968614  \
7            937    Milwaukee   Fullerton   Armitage       41.924792   
9            307  Irvi

In [27]:
# seperate segments based on weather stations

filename = "segment_street_mapping.csv"



df = pd.read_csv(filename)
print("The collected data dicreption ", df.info())
# Define the threshold distance for "near" in meters
NEAR_DISTANCE = 30000


# Calculate the Haversine distance between two points in meters
def haversine_distance(lat1, lon1, lat2, lon2):
    R = 6371e3  # Radius of the earth in km
    dLat = math.radians(lat2 - lat1)
    dLon = math.radians(lon2 - lon1)
    a = math.sin(dLat / 2) * math.sin(dLat / 2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dLon / 2) * math.sin(dLon / 2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    d = R * c  # Distance in meters
    return d

weather_stations = [(41.901997, -87.622817)]
# Find the segments near each latitude and longitude pair
for lat, lon in weather_stations:
    distances = np.array([])
    print(f"Processing weather station at -  ({lat}, {lon}):")
    for _, row in df.iterrows():
        start_lat = row['start_latitude']
        start_lon = row['start_longitude']
        end_lat = row['end_latitude']
        end_lon = row['end_longitude']

        start_distance = haversine_distance(lat, lon, start_lat, start_lon)
        end_distance = haversine_distance(lat, lon, end_lat, end_lon)

        distances = np.append(distances, min(start_distance, end_distance))

    # Filter the segments based on the threshold distance
    near_segments = df[distances <= NEAR_DISTANCE]

    # Print the near segments
    print(f"Segments near ({lat}, {lon}):")
    print(near_segments)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1032 entries, 0 to 1031
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   segment_id       1032 non-null   int64  
 1   street           1032 non-null   object 
 2   from_street      1032 non-null   object 
 3   to_street        1032 non-null   object 
 4   start_latitude   1032 non-null   float64
 5   start_longitude  1032 non-null   float64
 6   end_latitude     1032 non-null   float64
 7   end_longitude    1032 non-null   float64
dtypes: float64(4), int64(1), object(3)
memory usage: 64.6+ KB
The collected data dicreption  None
Processing weather station at -  (41.901997, -87.622817):
Segments near (41.901997, -87.622817):
      segment_id               street from_street            to_street   
1            365              Western    Lawrence               Foster  \
2           1037               Wacker       State              LaSalle   
3           1193